Get raw lines (title + summary) in ascii from json and upload to HF Hub

In [1]:
!pip install huggingface_hub datasets --quiet

In [2]:
import string
import unicodedata
import pandas as pd

# Turn a Unicode string to plain ASCII, thanks to https://stackoverflow.com/a/518232/2809427
def unicode2ascii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
        and c in all_letters
    )

In [3]:
all_letters = string.ascii_letters + "1234567890" + " .,;'\n"
n_letters = len(all_letters)

In [4]:
!wget -q https://huggingface.co/datasets/sswt/arxiv_sample_50K/resolve/main/arxiv_sample.tar.gz -O data.tar.gz && tar -xzf data.tar.gz

In [5]:
data = pd.read_json("./arxiv_sample.json")
print(data.shape)
data.sample(n=3)

(50000, 5)


title   published  \
19656  Generalized K-fan Multimodal Deep Model with S...  2015-03-26   
22624  Bootstrapping Monodromy Defects in the Wess-Zu...  2021-08-11   
19165  Attention-Enhanced Neural Network Models for T...  2021-10-06   

                                         authors  \
19656             [Gang Chen, Sargur N. Srihari]   
22624         [Aleix Gimenez-Grau, Pedro Liendo]   
19165  [Wenhui Peng, Zelong Yuan, Jianchun Wang]   

                                                 summary  \
19656  Multimodal learning with deep Boltzmann machin...   
22624  We use analytical bootstrap techniques to stud...   
19165  Deep neural network models have shown a great ...   

                                    link  
19656  http://arxiv.org/abs/1503.07906v1  
22624  http://arxiv.org/abs/2108.05107v3  
19165  http://arxiv.org/abs/2110.02471v3

In [6]:
BOS, EOS = ' ', '\n'
lines = data.apply(lambda row: unicode2ascii((row['title'] + ' ; ' + row['summary'])), axis=1) \
            .apply(lambda line: BOS + line.replace(EOS, ' ')) \
            .tolist()

In [7]:
with open('title_summary_ascii.txt', 'w') as fp:
    fp.write('\n'.join(lines) + '\n')

In [10]:
!tar -zcf title_summary_ascii.txt.tar.gz title_summary_ascii.txt

In [8]:
from datasets import load_dataset
from huggingface_hub import HfApi
from huggingface_hub import login
login()

In [11]:
api = HfApi()
api.upload_file(
    path_or_fileobj="title_summary_ascii.txt.tar.gz",
    path_in_repo="title_summary_ascii.txt.tar.gz",
    repo_id="sswt/arxiv_sample_50K",
    repo_type="dataset",
)

title_summary_ascii.txt.tar.gz:   0%|          | 0.00/17.5M [00:00<?, ?B/s]

'https://huggingface.co/datasets/sswt/arxiv_sample_50K/blob/main/title_summary_ascii.txt.tar.gz'